<h1> Using Labeled Data to Train a Network, Use The Network to Label New Videos, and Create Trajectories </h1> 
<p> Use another notebook create a project, extract frames, and label training/testing data </p>

# DLC with docker
This notebook illustrates how to use the Docker container to:
- train a network
- evaluate a network
- analyze a novel video

many of the functions have additional parameters / complexity, see the DLC docs for more inf on each.

This assumes you already have a project folder with labeled data! 


## info about the Docker Environment:
Docker is essentially a better alternative to virtual machines. It is able to containerize applications in a way that keeps them seperate the OS and other software. 

For tensorflow / deeplab cut, docker is critical for two reasons. 
- It 'claims' the GPU, making it closed for use by other processes.
- It queries the GPU properly, in some cases tf (and the python kernal itself) does not know how to properly communincate with the GPU on windows systems.

In [2]:
# make sure you graphic driver is accessable
!nvcc --version

nvcc: NVIDIA (R) Cuda compiler driver
Copyright (c) 2005-2017 NVIDIA Corporation
Built on Fri_Sep__1_21:08:32_Central_Daylight_Time_2017
Cuda compilation tools, release 9.0, V9.0.176


In [3]:
# check the tensorflow version
import tensorflow as tf
tf.__version__

'1.14.0'

<h1> The following is very important as it allow the current GPU process to grow dynamically </h1>
Without this option tf will likely run out of VRAM when trying to update the weight tensor. In theory, these options could cause the GPU to run out of memory entirely, but there is no other way to allow training to complete successfully. 

In [4]:
#allow video memory growth as network expands to avoid convolutional network errors
TF_FORCE_GPU_ALLOW_GROWTH = True
config = tf.ConfigProto()
config.gpu_options.allow_growth = True
session = tf.Session(config=config)

In [5]:
#let's make sure we see a GPU:
#tf.test.gpu_device_name()
from tensorflow.python.client import device_lib
device_lib.list_local_devices()

[name: "/device:CPU:0"
 device_type: "CPU"
 memory_limit: 268435456
 locality {
 }
 incarnation: 14070016427219047373, name: "/device:GPU:0"
 device_type: "GPU"
 memory_limit: 6586089472
 locality {
   bus_id: 1
   links {
   }
 }
 incarnation: 508278209697116966
 physical_device_desc: "device: 0, name: GeForce RTX 2080, pci bus id: 0000:41:00.0, compute capability: 7.5", name: "/device:GPU:1"
 device_type: "GPU"
 memory_limit: 6586089472
 locality {
   bus_id: 1
   links {
   }
 }
 incarnation: 11114233150249995340
 physical_device_desc: "device: 1, name: GeForce RTX 2080, pci bus id: 0000:81:00.0, compute capability: 7.5"]

## Start here for training DeepLabCut and analyzing new videos!
<p><br>If the first imports fail, there is again - sadly - an issue with you enviroment. Make sure all packages beside DLC are installed via conda. </p> 

In [6]:
#GUIs don't work on in Docker (or the cloud), so label your data locally on your computer! 
#This notebook is for you to train and run video analysis!
import os

In [7]:
# now we are ready to train!
#should see version 2.0.8
import deeplabcut
deeplabcut.__version__

'2.0.8'

<h1> change to your path: </h1>
<p> this should be the same path as the one in the createDLCproject notebook. The path is the path to the config.yaml file, not the project directory itself </p> 

In [9]:
path_config_file = r'F:\MysoreData\nbk\TEST_mitg11_04132020_DLC\cam1_mitg11_04132020-spencer_loggia-2020-04-18\\config.yaml'

## Create a training dataset
This function generates the training data information for DeepCut (which requires a mat file) based on the pandas dataframes that hold label information. The user can set the fraction of the training set size (from all labeled image in the hd5 file) in the config.yaml file. While creating the dataset, the user can create multiple shuffles. 

After running this script the training dataset is created and saved in the project directory under the subdirectory **'training-datasets'**

This function also creates new subdirectories under **dlc-models** and appends the project config.yaml file with the correct path to the training and testing pose configuration file. These files hold the parameters for training the network. Such an example file is provided with the toolbox and named as **pose_cfg.yaml**.

In [10]:
deeplabcut.create_training_dataset(path_config_file,Shuffles=[1])

F:\MysoreData\nbk\TEST_mitg11_04132020_DLC\cam1_mitg11_04132020-spencer_loggia-2020-04-18\labeled-data\mitg11-839--04132020085312.avi_clip_10/CollectedData_spencer_loggia.h5  not found (perhaps not annotated)
The training dataset is successfully created. Use the function 'train_network' to start training. Happy training!


### now go edit the pose_cfg.yaml to make display_iters: low (i.e. 10), and save_iters: 500

Now it is the time to start training the network!

## Start training
This function trains the network for a specific shuffle of the training dataset. 

In [11]:
#reset in case you started a session before...
#tf.reset_default_graph()

deeplabcut.train_network(path_config_file, shuffle=1, saveiters=1000, displayiters=10)

#this will run until you stop it (CTRL+C), or hit "STOP" icon, or when it hits the end (default, 1.3M iterations). 
#Whichever you chose, you will see what looks like an error message, but it's not an error - don't worry....


Config:
{'all_joints': [[0], [1], [2]],
 'all_joints_names': ['bodypart1', 'bodypart2', 'bodypart3'],
 'batch_size': 1,
 'bottomheight': 400,
 'crop': True,
 'crop_pad': 0,
 'cropratio': 0.4,
 'dataset': 'training-datasets\\iteration-0\\UnaugmentedDataSet_cam1_mitg11_04132020Apr18\\cam1_mitg11_04132020_spencer_loggia95shuffle1.mat',
 'dataset_type': 'default',
 'deterministic': False,
 'display_iters': 1000,
 'fg_fraction': 0.25,
 'global_scale': 0.8,
 'init_weights': 'C:\\Users\\pbs-mysorelab\\.conda\\envs\\nbkGPU\\lib\\site-packages\\deeplabcut\\pose_estimation_tensorflow\\models\\pretrained\\resnet_v1_50.ckpt',
 'intermediate_supervision': False,
 'intermediate_supervision_layer': 12,
 'leftwidth': 400,
 'location_refinement': True,
 'locref_huber_loss': True,
 'locref_loss_weight': 0.05,
 'locref_stdev': 7.2801,
 'log_dir': 'log',
 'max_input_size': 1500,
 'mean_pixel': [123.68, 116.779, 103.939],
 'metadataset': 'training-datasets\\iteration-0\\UnaugmentedDataSet_cam1_mitg11_04132

Starting with standard pose-dataset loader.


W0419 00:01:48.214658 29616 deprecation.py:323] From C:\Users\pbs-mysorelab\.conda\envs\nbkGPU\lib\site-packages\tensorflow\python\ops\nn_impl.py:180: add_dispatch_support.<locals>.wrapper (from tensorflow.python.ops.array_ops) is deprecated and will be removed in a future version.
Instructions for updating:
Use tf.where in 2.0, which has the same broadcast rule as np.where
W0419 00:01:48.263670 29616 deprecation.py:323] From C:\Users\pbs-mysorelab\.conda\envs\nbkGPU\lib\site-packages\deeplabcut\pose_estimation_tensorflow\nnet\losses.py:38: to_float (from tensorflow.python.ops.math_ops) is deprecated and will be removed in a future version.
Instructions for updating:
Use `tf.cast` instead.
W0419 00:02:03.557147 29616 deprecation.py:323] From C:\Users\pbs-mysorelab\.conda\envs\nbkGPU\lib\site-packages\tensorflow\python\training\saver.py:1276: checkpoint_exists (from tensorflow.python.training.checkpoint_management) is deprecated and will be removed in a future version.
Instructions for 

Display_iters overwritten as 10
Save_iters overwritten as 1000
Training parameter:
{'stride': 8.0, 'weigh_part_predictions': False, 'weigh_negatives': False, 'fg_fraction': 0.25, 'weigh_only_present_joints': False, 'mean_pixel': [123.68, 116.779, 103.939], 'shuffle': True, 'snapshot_prefix': 'F:\\MysoreData\\nbk\\TEST_mitg11_04132020_DLC\\cam1_mitg11_04132020-spencer_loggia-2020-04-18\\dlc-models\\iteration-0\\cam1_mitg11_04132020Apr18-trainset95shuffle1\\train\\snapshot', 'log_dir': 'log', 'global_scale': 0.8, 'location_refinement': True, 'locref_stdev': 7.2801, 'locref_loss_weight': 0.05, 'locref_huber_loss': True, 'optimizer': 'sgd', 'intermediate_supervision': False, 'intermediate_supervision_layer': 12, 'regularize': False, 'weight_decay': 0.0001, 'mirror': False, 'crop_pad': 0, 'scoremap_dir': 'test', 'batch_size': 1, 'dataset_type': 'default', 'deterministic': False, 'crop': True, 'cropratio': 0.4, 'minsize': 100, 'leftwidth': 400, 'rightwidth': 400, 'topheight': 400, 'bottomhei

iteration: 10 loss: 0.2508 lr: 0.005
iteration: 20 loss: 0.0361 lr: 0.005
iteration: 30 loss: 0.0298 lr: 0.005
iteration: 40 loss: 0.0302 lr: 0.005
iteration: 50 loss: 0.0230 lr: 0.005
iteration: 60 loss: 0.0263 lr: 0.005
iteration: 70 loss: 0.0250 lr: 0.005
iteration: 80 loss: 0.0232 lr: 0.005
iteration: 90 loss: 0.0312 lr: 0.005
iteration: 100 loss: 0.0229 lr: 0.005
iteration: 110 loss: 0.0320 lr: 0.005
iteration: 120 loss: 0.0229 lr: 0.005
iteration: 130 loss: 0.0253 lr: 0.005
iteration: 140 loss: 0.0224 lr: 0.005
iteration: 150 loss: 0.0225 lr: 0.005
iteration: 160 loss: 0.0277 lr: 0.005
iteration: 170 loss: 0.0268 lr: 0.005
iteration: 180 loss: 0.0243 lr: 0.005
iteration: 190 loss: 0.0211 lr: 0.005
iteration: 200 loss: 0.0201 lr: 0.005
iteration: 210 loss: 0.0222 lr: 0.005
iteration: 220 loss: 0.0152 lr: 0.005
iteration: 230 loss: 0.0211 lr: 0.005
iteration: 240 loss: 0.0191 lr: 0.005
iteration: 250 loss: 0.0223 lr: 0.005
iteration: 260 loss: 0.0203 lr: 0.005
iteration: 270 loss: 

...

iteration: 1023700 loss: 0.0011 lr: 0.001
iteration: 1023710 loss: 0.0008 lr: 0.001
iteration: 1023720 loss: 0.0006 lr: 0.001
iteration: 1023730 loss: 0.0007 lr: 0.001
iteration: 1023740 loss: 0.0009 lr: 0.001
iteration: 1023750 loss: 0.0005 lr: 0.001
iteration: 1023760 loss: 0.0006 lr: 0.001
iteration: 1023770 loss: 0.0007 lr: 0.001
iteration: 1023780 loss: 0.0007 lr: 0.001
iteration: 1023790 loss: 0.0006 lr: 0.001
iteration: 1023800 loss: 0.0007 lr: 0.001
iteration: 1023810 loss: 0.0007 lr: 0.001
iteration: 1023820 loss: 0.0006 lr: 0.001
iteration: 1023830 loss: 0.0009 lr: 0.001
iteration: 1023840 loss: 0.0007 lr: 0.001
iteration: 1023850 loss: 0.0005 lr: 0.001
iteration: 1023860 loss: 0.0004 lr: 0.001
iteration: 1023870 loss: 0.0006 lr: 0.001
iteration: 1023880 loss: 0.0006 lr: 0.001
iteration: 1023890 loss: 0.0005 lr: 0.001
iteration: 1023900 loss: 0.0006 lr: 0.001
iteration: 1023910 loss: 0.0005 lr: 0.001
iteration: 1023920 loss: 0.0010 lr: 0.001
iteration: 1023930 loss: 0.0005 lr

iteration: 1025650 loss: 0.0006 lr: 0.001
iteration: 1025660 loss: 0.0005 lr: 0.001
iteration: 1025670 loss: 0.0009 lr: 0.001
iteration: 1025680 loss: 0.0005 lr: 0.001
iteration: 1025690 loss: 0.0006 lr: 0.001
iteration: 1025700 loss: 0.0006 lr: 0.001
iteration: 1025710 loss: 0.0004 lr: 0.001
iteration: 1025720 loss: 0.0006 lr: 0.001
iteration: 1025730 loss: 0.0006 lr: 0.001
iteration: 1025740 loss: 0.0006 lr: 0.001
iteration: 1025750 loss: 0.0005 lr: 0.001
iteration: 1025760 loss: 0.0006 lr: 0.001
iteration: 1025770 loss: 0.0006 lr: 0.001
iteration: 1025780 loss: 0.0007 lr: 0.001
iteration: 1025790 loss: 0.0004 lr: 0.001
iteration: 1025800 loss: 0.0005 lr: 0.001
iteration: 1025810 loss: 0.0004 lr: 0.001
iteration: 1025820 loss: 0.0007 lr: 0.001
iteration: 1025830 loss: 0.0005 lr: 0.001
iteration: 1025840 loss: 0.0008 lr: 0.001
iteration: 1025850 loss: 0.0006 lr: 0.001
iteration: 1025860 loss: 0.0006 lr: 0.001
iteration: 1025870 loss: 0.0006 lr: 0.001
iteration: 1025880 loss: 0.0006 lr

iteration: 1027600 loss: 0.0006 lr: 0.001
iteration: 1027610 loss: 0.0009 lr: 0.001
iteration: 1027620 loss: 0.0006 lr: 0.001
iteration: 1027630 loss: 0.0006 lr: 0.001
iteration: 1027640 loss: 0.0006 lr: 0.001
iteration: 1027650 loss: 0.0006 lr: 0.001
iteration: 1027660 loss: 0.0006 lr: 0.001
iteration: 1027670 loss: 0.0007 lr: 0.001
iteration: 1027680 loss: 0.0006 lr: 0.001
iteration: 1027690 loss: 0.0009 lr: 0.001
iteration: 1027700 loss: 0.0006 lr: 0.001
iteration: 1027710 loss: 0.0007 lr: 0.001
iteration: 1027720 loss: 0.0006 lr: 0.001
iteration: 1027730 loss: 0.0006 lr: 0.001
iteration: 1027740 loss: 0.0005 lr: 0.001
iteration: 1027750 loss: 0.0006 lr: 0.001
iteration: 1027760 loss: 0.0007 lr: 0.001
iteration: 1027770 loss: 0.0006 lr: 0.001
iteration: 1027780 loss: 0.0006 lr: 0.001
iteration: 1027790 loss: 0.0006 lr: 0.001
iteration: 1027800 loss: 0.0006 lr: 0.001
iteration: 1027810 loss: 0.0006 lr: 0.001
iteration: 1027820 loss: 0.0009 lr: 0.001
iteration: 1027830 loss: 0.0008 lr

iteration: 1029550 loss: 0.0005 lr: 0.001
iteration: 1029560 loss: 0.0006 lr: 0.001
iteration: 1029570 loss: 0.0005 lr: 0.001
iteration: 1029580 loss: 0.0006 lr: 0.001
iteration: 1029590 loss: 0.0005 lr: 0.001
iteration: 1029600 loss: 0.0006 lr: 0.001
iteration: 1029610 loss: 0.0006 lr: 0.001
iteration: 1029620 loss: 0.0007 lr: 0.001
iteration: 1029630 loss: 0.0008 lr: 0.001
iteration: 1029640 loss: 0.0004 lr: 0.001
iteration: 1029650 loss: 0.0006 lr: 0.001
iteration: 1029660 loss: 0.0006 lr: 0.001
iteration: 1029670 loss: 0.0008 lr: 0.001
iteration: 1029680 loss: 0.0006 lr: 0.001
iteration: 1029690 loss: 0.0004 lr: 0.001
iteration: 1029700 loss: 0.0006 lr: 0.001
iteration: 1029710 loss: 0.0004 lr: 0.001
iteration: 1029720 loss: 0.0007 lr: 0.001
iteration: 1029730 loss: 0.0005 lr: 0.001
iteration: 1029740 loss: 0.0006 lr: 0.001
iteration: 1029750 loss: 0.0005 lr: 0.001
iteration: 1029760 loss: 0.0006 lr: 0.001
iteration: 1029770 loss: 0.0005 lr: 0.001
iteration: 1029780 loss: 0.0006 lr

The network is now trained and ready to evaluate. Use the function 'evaluate_network' to evaluate the network.


### A couple tips for possible troubleshooting (1): 

if you get **permission errors** when you run this step (above), first check if the weights downloaded. As some docker containers might not have privileges for this (it can be user specific). They should be under 'init_weights' (see path in the pose_cfg.yaml file). You can enter the DOCKER in the terminal:

see more here: https://github.com/MMathisLab/Docker4DeepLabCut2.0#using-the-docker-for-training-and-video-analysis

### Troubleshooting (2): 
if it appears the training does not start (i.e. "Starting training..." does not print immediately),
then you have another session running on your GPU. Go check "nvidia-smi" and look at the process names. You can only have 1 per GPU!)

## Start evaluating
This funtion evaluates a trained model for a specific shuffle/shuffles at a particular state or all the states on the data set (images)
and stores the results as .csv file in a subdirectory under **evaluation-results**

In [12]:
deeplabcut.evaluate_network(path_config_file)

# Here you want to see a low pixel error! Of course, it can only be as good as the labeler, so be sure your labels are good!

Config:
{'all_joints': [[0], [1], [2]],
 'all_joints_names': ['bodypart1', 'bodypart2', 'bodypart3'],
 'batch_size': 1,
 'bottomheight': 400,
 'crop': True,
 'crop_pad': 0,
 'cropratio': 0.4,
 'dataset': 'training-datasets\\iteration-0\\UnaugmentedDataSet_cam1_mitg11_04132020Apr18\\cam1_mitg11_04132020_spencer_loggia95shuffle1.mat',
 'dataset_type': 'default',
 'deterministic': False,
 'display_iters': 1000,
 'fg_fraction': 0.25,
 'global_scale': 0.8,
 'init_weights': 'C:\\Users\\pbs-mysorelab\\.conda\\envs\\nbkGPU\\lib\\site-packages\\deeplabcut\\pose_estimation_tensorflow\\models\\pretrained\\resnet_v1_50.ckpt',
 'intermediate_supervision': False,
 'intermediate_supervision_layer': 12,
 'leftwidth': 400,
 'location_refinement': True,
 'locref_huber_loss': True,
 'locref_loss_weight': 0.05,
 'locref_stdev': 7.2801,
 'log_dir': 'log',
 'max_input_size': 1500,
 'mean_pixel': [123.68, 116.779, 103.939],
 'metadataset': 'training-datasets\\iteration-0\\UnaugmentedDataSet_cam1_mitg11_04132

Running  DeepCut_resnet50_cam1_mitg11_04132020Apr18shuffle1_1030000  with # of trainingiterations: 1030000
Analyzing data...


24it [00:04,  4.99it/s]


Done and results stored for snapshot:  snapshot-1030000
Results for 1030000  training iterations: 95 1 train error: 1.83 pixels. Test error: 6.5  pixels.
With pcutoff of 0.1  train error: 1.83 pixels. Test error: 6.5 pixels
Thereby, the errors are given by the average distances between the labels by DLC and the scorer.
The network is evaluated and the results are stored in the subdirectory 'evaluation_results'.
If it generalizes well, choose the best model for prediction and update the config file with the appropriate index for the 'snapshotindex'.
Use the function 'analyze_video' to make predictions on new videos.
Otherwise consider retraining the network (see DeepLabCut workflow Fig 2)


## There is an optional refinement step
- if your pixel errors are not low enough, use DLC docs on how to refine yur network!
- You will need to adjust the labels outside of DOCKER! (you can use the createDLCproject notebook) 
-  see DLC protocol instructions on how to refine your data!

## Start Analyzing videos
This function analyzes the new video. The user can choose the best model from the evaluation results and specify the correct snapshot index for the variable **snapshotindex** in the **config.yaml** file. Otherwise, by default the most recent snapshot is used to analyse the video.

The results are stored in hd5 file in the same directory where the video resides. 

In [ ]:
import os
folder = 'F:\\MysoreData\\nbk\\mitg11_4-13-20\\cam1\\clips\\'
names = os.listdir(folder)
for i in names:
    i = folder + i
print(names)
videofile_path = names #Enter the list of videos to analyze.
deeplabcut.analyze_videos(path_config_file,videofile_path)

## Create labeled video
This funtion is for visualiztion purpose and can be used to create a video in .mp4 format with labels predicted by the network. This video is saved in the same directory where the original video resides. 

In [ ]:
deeplabcut.create_labeled_video(path_config_file,videofile_path)

## Plot the trajectories of the analyzed videos
This function plots the trajectories of all the body parts across the entire video. Each body part is identified by a unique color.

In [ ]:
%matplotlib notebook 
#for making interactive plots.
#deeplabcut.plot_trajectories(path_config_file,videofile_path, plotting=True)

deeplabcut.plot_trajectories(path_config_file,videofile_path,showfigures=True)